In [1]:
import pandas as pd

df = pd.read_json(r'data.json')

In [2]:
pd.set_option('display.max_colwidth', None)
df.head()

tokenized_text  \
0                                                                                                                                                                                                                                                                               [Mamadou, Diop, ,, a, resident, of, Dakar, ,, is, a, regular, at, the, ', Club, 54, ', nightclub, located, at, 45, Rue, de, la, Liberté, ., He, usually, arrives, around, midnight, and, often, leaves, around, 3, am, ., Mamadou, ', s, ID, card, number, is, WS-123456789-1, ,, and, he, pays, for, his, drinks, with, a, credit, card, :, 1234-5678-9012-3456, .]   
1                                                   [A, Cônsul, Britânico, em, Brasília, ,, Sir, William, Percival, ,, recebeu, recentemente, uma, solicitação, de, passaporte, de, Sir, John, Watson, ,, residente, em, Campinas, ,, São, Paulo, ., O, pedido, incluiu, documentos, de, identificação, ,, como, CPF, 123, ., 456, ., 789-01, ,, CNH, 0123, ., 456, ., 789-12, e, RG, 11, ., 223, ., 554-0, ., Além, disso, ,, apresentou, duas, fotos, recentes, ,, um, cartão, de, crédito, para, verificação, de, identidade, e, endereço, de, residência, atual, :, Rua, José, de, Anchieta, ,, 123, ,, Jardim, Oceânico, ,, Campinas, ,, SP, .]   
2           [Il, pompiere, Saif, Al, Khaili, ,, di, nazionalità, Emirati, ,, ha, prestato, servizio, presso, la, stazione, di, pompieri, di, Abu, Dhabi, per, i, passati, dieci, anni, ., Durante, la, sua, permanenza, ,, sono, state, registrate, le, seguenti, informazioni, :, il, suo, numero, di, licenza, di, guida, è, 123456, ,, il, suo, numero, di, telefono, personale, è, 055, 555, 55, 55, ,, la, sua, data, di, nascita, è, il, 28, dicembre, 1980, ,, la, sua, indirizzo, è, via, Al, Karama, 31, ,, Abu, Dhabi, ., Per, le, sue, prestazioni, mediche, ,, Saif, ha, fornito, il, numero, di, suo, Assicurazione, Sanitaria, :, ...]   
3                                                                                                                                                                                                                                                                         [Aquela, queria, ser, imam, em, uma, mesquita, em, Belgrado, ,, mas, precisava, de, documentos, para, se, registrar, ., Ele, forneceu, seus, dados, pessoais, :, nome, Ahmed, Mustafa, ,, número, de, passaporte, 123456789, ,, e, número, de, CPF, 111, ., 222, ., 333-45, ., Ele, também, compartilhou, seu, número, de, telefone, celular, +, 381, 61, 234, 567, 89, .]   
4  [Le, dossier, médical, de, Mme, Kabila, Nzanzu, ,, née, le, 1er, mai, 1985, à, Kinshasa, ,, contient, des, informations, sensibles, sur, sa, santé, ., Il, y, a, une, prescription, pour, du, lithium, 300mg, par, jour, pour, traiter, une, dépression, majeure, ,, ainsi, qu, ', une, note, de, rendez-vous, pour, une, consultation, psychiatrique, le, 15, septembre, prochain, à, l, ', hôpital, General, de, Kinshasa, ., Ses, informations, de, contact, sont, :, adresse, résidentielle, :, rue, du, Congo, ,, no, 12, ,, Kinshasa, ;, numéro, de, téléphone, :, +, 243, 81, 23, 54, 67, 89, ;, numéro, d, ', assurance, maladie, :, ...]   

                                                                                                                                                                                                                          ner  
0                                                                                                                               [[0, 1, person], [14, 15, nightclub], [45, 45, ID card number], [58, 58, credit card number]]  
1                                                                                                [[6, 8, person], [17, 19, person], [36, 41, CPF], [43, 48, CNH], [50, 55, RG], [79, 91, address], [79, 91, current address]]  
2                             [[2, 4, person], [68, 70, date], [76, 82, address], [47, 47, driver's license number], [108, 108, passport number], [10

In [3]:
# Function to combine tokens and labels
def combine_tokens_and_labels(row):
    tokens = row["tokenized_text"]
    ner_labels = row["ner"]
    combined_data = []
    for start, end, label in ner_labels:
        combined_token = " ".join(tokens[start:end + 1])
        combined_data.append((combined_token, label))
    return combined_data


# Apply the function to each row and create a new DataFrame
new_df = df.apply(combine_tokens_and_labels, axis=1).explode().reset_index(
    drop=True).to_frame()

new_df[['token', 'label']] = new_df[0].apply(lambda x: pd.Series(x))
new_df = new_df.drop(columns=[0])
new_df = new_df.drop_duplicates(subset=["token","label"])

In [4]:
new_df.head()

token               label
0          Mamadou Diop              person
1               Club 54           nightclub
2        WS-123456789-1      ID card number
3   1234-5678-9012-3456  credit card number
4  Sir William Percival              person

In [5]:
# Get unique labels in the dataset
label_counts = new_df['label'].value_counts()
pd.set_option('display.max_rows', None)
# Display the unique labels
print(label_counts)

label
person                                                                 16587
organization                                                            9412
address                                                                 7883
phone number                                                            6395
email                                                                   5831
passport number                                                         3944
social security number                                                  3039
birth date                                                              2671
location                                                                2569
date                                                                    2113
date of birth                                                           2063
mobile phone number                                                     1604
health insurance ID number                                            

In [6]:
label_mapping = {
    "mobile phone number": "phone number",
    "email address": "email",
    "phone number": "phone number",  # Keep original mapping for clarity
    "credit card number": "credit card number",  # Similarly, for credit card
    "IP address": "IP address",
    "bank account number": "bank account number",
    # "NRIC number": "NRIC number",
    "location": "location",
    "city": "location",  # Categorizing 'city' as a 'location'
    "website": "website",
    "person": "person",
    "email": "email",
    "address" : "location",
    "passport number": "passport number",
    "IBAN": "bank account number",
    "personal ID number": "personal ID number",
    "social security number": "personal ID number",
    "national ID number": "personal ID number",
    "bank": "location",
    "educational institution": "location",
    "country": "location",
    "hospital": "location",
    "national identification number": "personal ID number",
    "identification number": "personal ID number",
    "ID number": "personal ID number"
}

# Filter and categorize the labels
filtered_df = new_df[new_df['label'].isin(label_mapping.keys())].copy()

# Apply the mapping to categorize similar labels into the same label
filtered_df['label'] = filtered_df['label'].map(label_mapping)
filtered_df.loc[~filtered_df["label"].isin(["person", "location"]), "token"] = filtered_df.loc[~filtered_df["label"].isin([
    "person", "location"]), "token"].str.replace(" ", "")
filtered_df = filtered_df.drop_duplicates(subset=["token", "label"])
filtered_df.reset_index(drop=True, inplace=True)

In [7]:
sample_df = filtered_df.sample(frac=0.2, random_state = 1)
sample_df.reset_index(drop = True, inplace = True)
print(sample_df)

                                                                                                           token  \
0                                                                                                55-11-9876-1234   
1                                                                                                         654321   
2                                                                                                    22522112345   
3                                                                                               liwei@pek.lib.cn   
4                                                                                               Mogwadi Tshekedi   
5                                                                                                  Kwame Agyeman   
6                                                                                     numérodepasseport111122233   
7                                                                       

In [8]:
print(sample_df['label'].value_counts())

label
person                 3339
location               2256
phone number           1492
email                  1215
passport number         750
personal ID number      739
bank account number     282
credit card number      272
website                  29
IP address               14
Name: count, dtype: int64


In [9]:
import sys
sys.path.append("..")

from anonymizer import AnonymizerEngine

engine = AnonymizerEngine()

In [10]:
sample_df['anonymized_token'] = sample_df['token'].apply(engine.anonymize)

print(sample_df)

                                                                                                           token  \
0                                                                                                55-11-9876-1234   
1                                                                                                         654321   
2                                                                                                    22522112345   
3                                                                                               liwei@pek.lib.cn   
4                                                                                               Mogwadi Tshekedi   
5                                                                                                  Kwame Agyeman   
6                                                                                     numérodepasseport111122233   
7                                                                       

In [11]:
success_counts = sample_df[sample_df["token"] !=
                           sample_df["anonymized_token"]].groupby("label").size()

total_counts = sample_df.groupby("label").size()

success_rates = (success_counts / total_counts) * 100

print(success_rates)

label
IP address             92.857143
bank account number    90.425532
credit card number     70.588235
email                  99.753086
location               80.718085
passport number        92.666667
person                 95.178197
personal ID number     86.062246
phone number           97.050938
website                93.103448
dtype: float64


In [12]:
sample_df.to_excel('output.xlsx', index=False)